# Web Scaping and noun phrase (NP) chunking of Amazon Movie Reviews
   By Heidi Nguyen

<a id="top"></a>

# Table of Contents 

- [I. Scraping Action Movie Reviews from Amazon](#AMZAction)

- [II. Extracting noun phrase (NP) chunks from action movie reviews](#npchunks)

- [III. Summary of Results](#result)

- [IV. Reference](#ref)

- [V. Appendix](#appd)


In [2]:
# libraries
from pandas import DataFrame,Series
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pylab as plt
from collections import Counter
import os # to set wd # # os.environ['KERAS_BACKEND']='tensorflow' for keras
import re

# get time stamp
import time
# import Image
from IPython.display import Image

# BeautifulSoup 
from bs4 import BeautifulSoup
import  codecs # that’s to take care of things like accented characters, which are represented in different ways on

# lxml 
from lxml import html
import requests 

# Keras 
from keras.models import Sequential
from keras.layers.core import Dense, Dropout, Activation
from keras.optimizers import SGD
from sklearn.metrics import roc_auc_score
from keras import optimizers

# access keyboard shortcuts: Esc + H
# Mac: Cmd + Shift + P ==> private browsing => Firefox does not track 
# Linux and Windows: or Ctrl + Shift + P on Linux and Windows

# Set wd
path = "/Users/heidinguyen/Downloads/"
os.chdir(path)
print (os.getcwd()); # Prints the working directory



Using TensorFlow backend.


/Users/heidinguyen/Downloads


In [3]:
try:
    import scrapy
    print (scrapy.__version__)
    
except:
    !pip install scrapy
    import scrapy
from scrapy.crawler import CrawlerProcess

1.5.1


In [4]:
# Settings for notebook
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"
# Show Python version
import platform
platform.python_version()

'2.7.14'

<a id="AMZAction"></a>

## Scraping Action Movie Reviews from Amazon

### Method Summary: 

I choose to get review data for all the Action and Advanture movies on Amazon "Movies & TV" Department. 
Movie reviews on Amazon are available to scrap using its node series and ASIN series. 
There are 144 movies with a total of 146072 reviews for this Action and Advanture genre. Each movie has its own product reviews page @https://www.amazon.com/product-reviews/, e.g: Transformers: The Last Knight by Mark Wahlberg is at: https://www.amazon.com/product-reviews/B07215NWRL. This movie has 1,512 reviews (152 pages). 

For the purpose of this exercise, I only scrap 1000 urls of 8 movies, total of 9923 individual reviews. 
The complete copy of all the urls for all reviews of all 144 action movies on Amazon is in the file "Movies_urls_all.cvs"

      
 <a href="#top">Back to top</a>

## Loop through each item of the movie category to get all ASIN and its product reviews urls

In [ ]:
# Setup a pipeline
import json

class JsonWriterPipeline(object):

    def open_spider(self, spider):
        self.file = open('actionmovie_asin_result.jl', 'w')

    def close_spider(self, spider):
        self.file.close()

    def process_item(self, item, spider):
        line = json.dumps(dict(item)) + "\n"
        self.file.write(line)
        return item

In [ ]:
def get_node(string):
    s2 = "node="
    location = string.find(s2)
    return string[location+5:location+15]

def get_pf_rd_i(string):
    s2 = "pf_rd_i="
    location = string.find(s2)
    return string[location+8:location+19]



In [ ]:
# -*- coding: utf-8 -*-
import logging

class QuotesSpider(scrapy.Spider):
    name = "actionmoviequotes"
    allowed_urls = ['amazon.com']
    
    start_urls = []
    
    
    # START HARD CODED SECTION -get category URLs
    # Start from Movie department 
    category_start_url = [
        'https://www.amazon.com/action-adventure-dvd-bluray/b/ref=MoviesHPBB_Genres_Action?ie=UTF8&node=2650363011&pf_rd_m=ATVPDKIKX0DER&pf_rd_s=merchandised-search-left-3&pf_rd_r=KGTG4WSW10NRSAJSHTAG&pf_rd_r=KGTG4WSW10NRSAJSHTAG&pf_rd_t=101&pf_rd_p=f1849530-129c-4959-9d34-94ca73a3e67e&pf_rd_p=f1849530-129c-4959-9d34-94ca73a3e67e&pf_rd_i=2625373011']
    # manually get nod and pf_rd_i for action movie
    node = '2650363011' 
    pf_rd_i = '2625373011' 

    category_URL_list = ['https://www.amazon.com/s/ref=lp_' +
    node + '_pg_' + str(page_no) + '?rh=n%3A' + pf_rd_i + "%2Cn%3A%" + pf_rd_i + "%2Cn%3A" + node + "&page=" + str(page_no) + '&ie=UTF8&qi'
                           for page_no in range(2, 400)] # There are 400 pages for movies 

    start_urls = start_urls + category_start_url + category_URL_list  # add new links
        
    # END HARD CODED SECTION

    
    custom_settings = {
        'LOG_LEVEL': logging.WARNING,
        'ITEM_PIPELINES': {'__main__.JsonWriterPipeline': 1}, # Used for pipeline 1
        'FEED_FORMAT':'json',                                 # Used for pipeline 2
        'FEED_URI': 'actionmovie_asin_result.json'                        # Used for pipeline 2
    }
    
    def parse(self, response):
    #         for quote in response.css('div.quote'):
        
        product_node_list = response.xpath('//li[contains(@id, "result_")]')
        for product in product_node_list:
                    
            yield {
                'category': product.xpath('//h4[@class="a-size-small a-color-base a-text-bold"]/text()').extract_first(),
                
                'product_desc': product.xpath('.//a[@class="a-link-normal s-access-detail-page  s-color-twister-title-link a-text-normal"]/@title').extract_first(),
                'num_review': product.xpath('.//a[@class="a-size-small a-link-normal a-text-normal" and contains(@href, "customerReviews")]/text()').extract_first(),
                'company': product.xpath('.//span[@class="a-size-small a-color-secondary"]/text()').extract()[1],  # first element is 'by' (by Arris)
                 'rating': product.xpath('.//i[contains(@class, "a-icon-star")]/span/text()').extract_first() ,
                'ASIN': product.xpath('./@data-asin').extract_first(),
            }


In [ ]:
process = CrawlerProcess({
    'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'
})

process.crawl(QuotesSpider)
process.start()


In [ ]:
%ll actionmovie_asin_result.*

In [ ]:
!tail -n 2 actionmovie_asin_result.jl

In [ ]:
!tail -n 2 actionmovie_asin_result.json

In [ ]:
with open("actionmovie_asin_result.json", "r") as f:
    data = json.load(f)

df_asin_ACmovie = pd.DataFrame.from_dict(data, orient='columns') # ,orient='columns'
df_asin_ACmovie.to_csv("ACmovie_urls.csv", header=True, index=False, encoding='utf-8')
# df_asin_ACmovie.head()
# df_asin_ACmovie.info()

In [5]:
# read in the csv file: 
# df_asin_ACmovie = pd.DataFrame.from_dict(actionmovie_asin_result_json, orient='columns')
# df_asin_ACmovie.to_csv("ACmovie_urls.csv", header=True, index=False, encoding='utf-8')
df_asin_ACmovie = pd.read_csv("ACmovie_urls.csv")
df_asin_ACmovie.head()
df_asin_ACmovie.info()

ASIN     category company num_review                   product_desc  \
0  B07D2KJGB9  Movies & TV       R        407           Escape Plan 2: Hades   
1  B07F19R3D9  Movies & TV   PG-13        138           Ant-Man and the Wasp   
2  B07215NWRL  Movies & TV   PG-13      1,510  Transformers: The Last Knight   
3  B003WJ6AD2  Movies & TV      PG      1,576                         Legend   
4  B001I8458G  Movies & TV   PG-13        650                      Get Smart   

               rating  
0  2.6 out of 5 stars  
1  3.9 out of 5 stars  
2  3.4 out of 5 stars  
3  4.3 out of 5 stars  
4  4.4 out of 5 stars

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 144 entries, 0 to 143
Data columns (total 6 columns):
ASIN            144 non-null object
category        144 non-null object
company         144 non-null object
num_review      144 non-null object
product_desc    144 non-null object
rating          144 non-null object
dtypes: object(6)
memory usage: 6.8+ KB


**There are 144 Action movies available for watching on Amazon**

In [6]:
# df_asin_movie = pd.read_csv("Movie_Dept_asin.csv")
# #remove the trailing ' out of 5 stars' 
df_asin_ACmovie['rating'] = df_asin_ACmovie['rating'].str.rstrip(' out of 5 stars') # after exporting to csv, csv will make it float type

# change the num_review to int, I will need to use this to determin the number of pages to scrap for each ASIN 
df_asin_ACmovie['num_review'] = df_asin_ACmovie['num_review'].str.replace(',', '') #after exporting to csv, csv will make it float type

# export it to csv again and read it back in the gain to have all the type correct 
df_asin_ACmovie.to_csv("AcMovie_asin_clean.csv", header=True, index=False, encoding='utf-8')
df_asin_ACmovie = pd.read_csv("AcMovie_asin_clean.csv")

df_asin_ACmovie.info()
df_asin_ACmovie.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 144 entries, 0 to 143
Data columns (total 6 columns):
ASIN            144 non-null object
category        144 non-null object
company         144 non-null object
num_review      144 non-null int64
product_desc    144 non-null object
rating          144 non-null float64
dtypes: float64(1), int64(1), object(4)
memory usage: 6.8+ KB


ASIN     category company  num_review                   product_desc  \
0  B07D2KJGB9  Movies & TV       R         407           Escape Plan 2: Hades   
1  B07F19R3D9  Movies & TV   PG-13         138           Ant-Man and the Wasp   
2  B07215NWRL  Movies & TV   PG-13        1510  Transformers: The Last Knight   
3  B003WJ6AD2  Movies & TV      PG        1576                         Legend   
4  B001I8458G  Movies & TV   PG-13         650                      Get Smart   

   rating  
0     2.6  
1     3.9  
2     3.4  
3     4.3  
4     4.4

**Amazon has all the reviews under their product review page at: https://www.amazon.com/product-reviews/ 
All I have to do is to add an ASIN at the end and click through the pages to collect product reviews for each of the ASIN**

In [ ]:
## Get all the reviews for each of the ASIN. 

def get_asin(string):
#     s2 = "https://www.amazon.com/product-reviews/"
#     location1 = string.find(s2)
    s3 = "/ref=cm_cr_arp_d_paging_btm_3?pageNumber="
    location2 = string.find(s3)
    if location2 == -1: 
        
        return string[39: ]
    else: 
        return string[39: location2]


In [ ]:
# first page full list: 

start_URL_list = []

for a in df_asin_ACmovie.ASIN:
    first_url = "https://www.amazon.com/product-reviews/" + str(a) 
    start_URL_list.append(first_url)


# # df_url['add_pages'] = df_url["all_urls"].apply(get_asin)

df_url_firstpage = pd.DataFrame(np.array(start_URL_list), columns = ["page_urls"])

df_url_firstpage['ASIN'] = df_url_firstpage ["page_urls"].apply(get_asin)
    
df_url_firstpage.head()
len(df_url_firstpage)

In [ ]:
# Create a list to store the data
add_pages = []

for a, b in zip(df_asin_ACmovie.ASIN, df_asin_ACmovie.num_review) :
    # if more than a value,
    if np.isnan(b) or int(b) < 10: # this needs to be coverted to np. value since python cant convert NaN float to int
        continue
    else: 
        for i in range(2, (int(b) // 10 + 2)):
            next_url = "https://www.amazon.com/product-reviews/" + str(a) + "/ref=cm_cr_arp_d_paging_btm_3?pageNumber=" + str(i)
        
            add_pages.append(next_url)


# all the urls pages to scrap
df_urls_movie = pd.DataFrame(np.array(add_pages), columns = ["page_urls"])
df_urls_movie['ASIN'] = df_urls_movie["page_urls"].apply(get_asin)

# export it to csv and read it back in the gain to make sure that all the links are ok. 
df_urls_movie.to_csv("Movies_urls_all.csv", header=True, index=False, encoding='utf-8')
df_urls_movie = pd.read_csv("Movies_urls_all.csv")

df_urls_movie.head()
len(df_urls_movie)

### Using all the ASIN and its product review urls to scrape product review details

In [7]:
from lxml import html
import requests 
import pandas as pd

In [8]:
#read in the file 
df_urls_movie = pd.read_csv("Movies_urls_all.csv")
df_urls_movie.head()
len(df_urls_movie)

page_urls        ASIN
0  https://www.amazon.com/product-reviews/B07D2KJ...  B07D2KJGB9
1  https://www.amazon.com/product-reviews/B07D2KJ...  B07D2KJGB9
2  https://www.amazon.com/product-reviews/B07D2KJ...  B07D2KJGB9
3  https://www.amazon.com/product-reviews/B07D2KJ...  B07D2KJGB9
4  https://www.amazon.com/product-reviews/B07D2KJ...  B07D2KJGB9

14544

**there are 14544 urls (or pages) of reviews for all the 144 Action and Adventure movies on Amazon**

## Scrape 1000 - 5000 pages at a time

In [19]:
df5 = df_urls_movie[1:1000] # change this everytime you scrape
df5.head()

page_urls        ASIN
201  https://www.amazon.com/product-reviews/B07215N...  B07215NWRL
202  https://www.amazon.com/product-reviews/B07215N...  B07215NWRL
203  https://www.amazon.com/product-reviews/B07215N...  B07215NWRL
204  https://www.amazon.com/product-reviews/B003WJ6...  B003WJ6AD2
205  https://www.amazon.com/product-reviews/B003WJ6...  B003WJ6AD2

In [20]:
%%time 

pages = df5.page_urls.values


columns = ['rating','title', 'author','date','body','helpful']
reviews_df = pd.DataFrame(columns=columns)

# 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)' 
user_agent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10.13; rv:61.0) Gecko/20100101 Firefox/61.0 (compatible; MSIE 7.0; Windows NT 5.1)'
headers = {'User-Agent': user_agent}


for item in pages:    
    page = requests.get(item, headers = headers)    
    parser = html.fromstring(page.content)    
    xpath_reviews = '//div[@data-hook="review"]'    
    reviews = parser.xpath(xpath_reviews)    
    xpath_rating  = './/i[@data-hook="review-star-rating"]//text()'     
    xpath_title   = './/a[@data-hook="review-title"]//text()'    
    xpath_author  = './/a[@data-hook="review-author"]//text()'   
    xpath_date    = './/span[@data-hook="review-date"]//text()'    
    xpath_body    = './/span[@data-hook="review-body"]//text()'    
    xpath_helpful = './/span[@data-hook="helpful-vote-statement"]//text()'    

    for review in reviews:        
        rating  = review.xpath(xpath_rating)       
        title   = review.xpath(xpath_title)        
        author  = review.xpath(xpath_author)        
        date    = review.xpath(xpath_date)        
        body    = review.xpath(xpath_body)       
        helpful = review.xpath(xpath_helpful)        
        
        review_dict = {'rating': rating,                   
                       'title': title,                   
                       'author': author,                                
                       'date': date,
                       'body': body,                   
                       'helpful': helpful,
                       'page_url': item,
                      }            
        
        reviews_df = reviews_df.append(review_dict, ignore_index=True)


CPU times: user 1min 24s, sys: 3.81 s, total: 1min 27s
Wall time: 9min 31s


## Raw Data processing

In [21]:
import re
def strcln(df):        
    for i in df.columns:            
        df[i] = df[i].map(lambda x: str(x)[:-2])      # Heidi(10/27) dont use this      
        df[i] = df[i].map(lambda x: str(x)[2:])

# call the function on the dataframe to remove the bracket and a space before and after in each data cell
strcln(reviews_df)


In [22]:
# remove the trailing ' out of 5 stars' 
reviews_df['rating'] = reviews_df['rating'].str.rstrip(' out of 5 stars').astype(float).astype(int)


In [23]:
# removing the 'on' and convert date to datetime
reviews_df['date'] = reviews_df['date'].str.lstrip('on')
reviews_df['date'] = pd.to_datetime(reviews_df['date'])

In [24]:
# export to csv ==> change the file name if needed 
timestr = time.strftime("%Y%m%d-%H%M%S")
new_file_name = "ACmovie_reviews_1_1000_" + timestr + ".csv"

reviews_df.to_csv(new_file_name, header=True, index=False, encoding='utf-8')


<a id="npchunks"></a>

# Extracting noun phrase (NP) chunks from action movie reviews

Extract noun phrase (NP) chunks from your reviews using the following procedure:
        
        a. In Python, grab the main review text from each link.
        b. Next run each review text through a tokenizer, and then try to NP-chunk it with a
        shallow parser.
        c. You probably will have too many unknown words, owing to proper names of characters,
        actors, and so on that are not in your working dictionary. Make sure the main names that are relevant to the movies in your collection of reviews are added to the working lexicon, and then run the NP chunker again.

 <a href="#top">Back to top</a>


In [32]:
#read in the file 
df_reviews = pd.read_csv("ACmovie_reviews_1000.csv")
df_reviews.head()
df_reviews.info()

rating                                              title           author  \
0       5   Lots of violence with a touch of science fiction    Bruce Winning   
1       5                    Glad for all the 1 star reviews          Aqua786   
2       4                                          Excellent  Toki Longsmokes   
3       1                     This Movie Was Named Correctly    David Moehlig   
4       1  One star reviews are not always correct, but t...      D. L. Smith   

      date                                               body  \
0  10/9/18  2.35/5.1 (theater quality) Which is what makes...   
1  9/30/18  The "one star" reviews lowered my expectations...   
2  9/28/18  Not the same as the first but it is just as go...   
3  10/7/18  While watching this movie i thought i was acua...   
4  9/29/18  Almost amateur acting with thin dialogue.  I d...   

                                             helpful  \
0  One person found this helpful', '2 people foun...   
1  One person found this helpful', '2 people foun...   
2  One person found this helpful', '2 people foun...   
3  One person found this helpful', '2 people foun...   
4                      One person found this helpful   

                                            page_url  
0  tps://www.amazon.com/product-reviews/B07D2KJGB...  
1  tps://www.amazon.com/product-reviews/B07D2KJGB...  
2  tps://www.amazon.com/product-reviews/B07D2KJGB...  
3  tps://www.amazon.com/product-reviews/B07D2KJGB...  
4  tps://www.amazon.com/product-reviews/B07D2KJGB...

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9923 entries, 0 to 9922
Data columns (total 7 columns):
rating      9923 non-null int64
title       9923 non-null object
author      9893 non-null object
date        9923 non-null object
body        9923 non-null object
helpful     6491 non-null object
page_url    9923 non-null object
dtypes: int64(1), object(6)
memory usage: 542.7+ KB


In [33]:
df_reviews_list = df_reviews.body.values
len(df_reviews_list)


9923

**There is a total of 9923 reviews from 1000 urls, for about 8 movies**

In [34]:
# review the reviews in the list
for document in df_reviews_list[1:5]: 
    print document + "EOL_HEIDI\n"

The "one star" reviews lowered my expectations, the first and second series in the Escape Plan franchise were really good, but this one definitely missed the high mark. However, because everyone dogged this movie, I watched it with a simplified mind. For that, it is a great movie!EOL_HEIDI

Not the same as the first but it is just as good in my opinion.  And for the record Stallone and Bautista appear throughout the whole movie.EOL_HEIDI

While watching this movie i thought i was acually in hades and started forming my own escape plan to get out of watching the rest of the movie i struggled through the horrible plot and had finally had enough the moment it show stalone in the ring with the antagonist saying lets see how you do without your tech at that point i stoped the movie because i could no longer watch this trashfire called a movie i didnt even bother watching the fight i new how it would end stalone beating up the tech guy. The only good parts were with Dave Bautista and im sure

In [35]:
# preprocess the documents to remove stopwords 

def tokenize_text(document):
    sentences = nltk.sent_tokenize(document)
    word_tokens = [nltk.word_tokenize(sentence) for sentence in sentences]
    return word_tokens

# function to remove stopwords from tokens 
def remove_stopwords(tokens):
    stopword_list = nltk.corpus.stopwords.words('english') # nltk.corpus.stopwords.words('english')
    # first, lower the case, then remove the words from the stopword list
    filtered_tokens = [token for token in tokens if token.lower() not in stopword_list]
    return filtered_tokens


from nltk.tokenize.treebank import TreebankWordDetokenizer
def detokenize (filtered_list):
        # detokenize to put back the sentences
    de_sentence = []
    for wordlist in filtered_list:
        de_wordlist = TreebankWordDetokenizer().detokenize(wordlist)
        de_sentence.append(de_wordlist)

        # get back the text
        # ",".join(de_sentence).replace("\xe2\x80\x93", "-").replace(".,", ".")
    sentences =  ",".join(de_sentence).replace(".,", ". ")
    return sentences


In [36]:
from __future__ import division
import networkx
import nltk
from pattern.en import parsetree

# looking at 10 reviews 
for document in df_reviews_list[1:10]:
    tokens_list = tokenize_text(document)
    
#     print tokens
    filtered_list = [remove_stopwords(token) for token in tokens_list]
    filtered_document = detokenize (filtered_list) 
    # start np chunk with parsetree 
    sentences = nltk.sent_tokenize(filtered_document)
    
    print ("start of review:")
    for sentence in sentences:
        tree = parsetree(sentence)
#         print type(tree)
        # Get chunks in an easier-to-understand format:
        # print all chunks
        for sentence_tree in tree:
            print (sentence_tree.chunk)
    print ("--end of review.")   

start of review:
[Chunk('\/NP'), Chunk('one star"reviews/NP'), Chunk('lowered/VP'), Chunk('expectations/NP'), Chunk('first second series Escape Plan franchise/NP'), Chunk('really good/ADJP'), Chunk('definitely missed/VP'), Chunk('high mark/NP')]
[Chunk('However/ADVP'), Chunk('everyone/NP'), Chunk('dogged/VP'), Chunk('movie/NP'), Chunk('watched/VP'), Chunk('simplified mind/NP')]
[Chunk('great movie/NP')]
--end of review.
start of review:
[Chunk('first good opinion/NP')]
[Chunk('record Stallone Bautista/NP'), Chunk('appear/VP'), Chunk('throughout/PP'), Chunk('whole movie/NP')]
--end of review.
start of review:
[Chunk('watching/VP'), Chunk('movie/NP'), Chunk('thought/VP'), Chunk('acually/ADJP'), Chunk('hades started forming escape/VP'), Chunk('plan get/NP'), Chunk('watching/VP'), Chunk('rest movie/NP'), Chunk('struggled/VP'), Chunk('horrible plot/NP'), Chunk('finally enough/ADJP'), Chunk('moment/VP'), Chunk('show stalone ring antagonist/NP'), Chunk('saying lets see/VP'), Chunk('without te

In [52]:
%%time
## output all the np-chunk: 

for document in df_reviews_list:
    tokens_list = tokenize_text(document)
    
#     print tokens
    filtered_list = [remove_stopwords(token) for token in tokens_list]
    filtered_document = detokenize (filtered_list) 
    # start np chunk with parsetree 
    sentences = nltk.sent_tokenize(filtered_document)
 
    print ("start of review:") 
    
    for sentence in sentences:
        tree = parsetree(sentence)
        print (tree)
        
    print ("--end of review.") 

#  import pickle
# with open('outfile', 'wb') as fp:
#     pickle.dump(np_chunk, fp)
# # To read it back:
# with open ('outfile', 'rb') as fp:
#     itemlist = pickle.load(fp)
# use dataframe and to_pickle
# df_np_chunk.to_pickle('hw5outfile.pickle')

# ll *pickle      


start of review:
[Sentence('2.35&slash;5.1/CD/O/O (/(/O/O theater/NN/B-NP/O quality/NN/I-NP/O )/)/O/O makes/VBZ/B-VP/O way/NN/B-NP/O supposed/VBN/B-VP/O get/VB/I-VP/O ././O/O')]
[Sentence('like/DT/B-NP/O violence/NN/I-NP/O action/NN/I-NP/O ././O/O')]
[Sentence('like/IN/B-PP/O punching/VBG/B-VP/O kicking/VBG/I-VP/O ././O/O')]
[Sentence('like/DT/B-NP/O shooting/NN/I-NP/O stabbing/VBG/B-VP/O ././O/O')]
[Sentence('like/DT/B-NP/O pursuit/NN/I-NP/O explosion/NN/I-NP/O ././O/O')]
[Sentence('appreciate/VB/B-VP/O recommendation/NN/B-NP/O email/NNP/I-NP/O Amazon/NNP/I-NP/O Prime/NNP/I-NP/O Video/NNP/I-NP/O ././O/O')]
--end of review.
start of review:
[Sentence('\\/NN/B-NP/O "/"/O/O one/CD/B-NP/O star"reviews/NNS/I-NP/O lowered/VBD/B-VP/O expectations/NNS/B-NP/O ,/,/O/O first/JJ/B-NP/O second/JJ/I-NP/O series/NNP/I-NP/O Escape/NNP/I-NP/O Plan/NNP/I-NP/O franchise/NN/I-NP/O really/RB/B-ADJP/O good/JJ/I-ADJP/O ,/,/O/O one/CD/O/O definitely/RB/B-VP/O missed/VBD/I-VP/O high/JJ/B-NP/O mark/NN/I-NP/O .

[Sentence('LOVE/NNP/B-NP/O Escape/NNP/I-NP/O Plan/NNP/I-NP/O 1/CD/O/O 2/CD/O/O ././O/O')]
--end of review.
start of review:
[Sentence('next/JJ/B-NP/O movie/NN/I-NP/O called/VBN/B-VP/O Escape/NNP/B-NP/O Plan/NNP/I-NP/O 3/CD/O/O :/:/O/O hope/NN/B-NP/O find/NN/I-NP/O better/JJR/I-NP/O Directors/NNS/I-NP/O ,/,/O/O Editors/NNS/B-NP/O ,/,/O/O writers/NNS/B-NP/O')]
--end of review.
start of review:
[Sentence('stupid/JJ/B-ADJP/O')]
--end of review.
start of review:
[Sentence('ok/NN/B-NP/O')]
--end of review.
start of review:
[Sentence('Good/JJ/B-NP/O job/NN/I-NP/O')]
--end of review.
start of review:
[Sentence('good/JJ/B-NP/O movie/NN/I-NP/O')]
--end of review.
start of review:
[Sentence('ok/NN/B-NP/O movie/NN/I-NP/O ././O/O')]
--end of review.
start of review:
[Sentence('expected/VBN/B-VP/O')]
--end of review.
start of review:
[Sentence('okay/JJ/B-ADJP/O')]
--end of review.
start of review:
[Sentence('Slow/JJ/B-NP/O moving/NN/I-NP/O')]
--end of review.
start of review:
[Sentence('expected/VBN

start of review:
[Sentence('ok/NN/B-NP/O movie/NN/I-NP/O ././O/O')]
--end of review.
start of review:
[Sentence('greatest/JJS/B-ADJP/O ././O/O')]
[Sentence('Part/NN/B-NP/O 1/CD/O/O better/JJR/B-ADJP/O ././O/O')]
[Sentence('one/CD/O/O animated/JJ/B-ADJP/O fake...dont/CD/B-NP/O purchase/NN/I-NP/O ././O/O')]
--end of review.
start of review:
[Sentence('expected/VBN/B-VP/O')]
--end of review.
start of review:
[Sentence('okay/JJ/B-ADJP/O')]
--end of review.
start of review:
[Sentence('Slow/JJ/B-NP/O moving/NN/I-NP/O')]
--end of review.
start of review:
[Sentence('expected/VBN/B-VP/O')]
--end of review.
start of review:
[Sentence('complicated/VBN/B-VP/O')]
--end of review.
start of review:
[Sentence('Good/JJ/B-NP/O movie/NN/I-NP/O')]
--end of review.
start of review:
[Sentence('loved/VBD/B-VP/O')]
--end of review.
start of review:
[Sentence('ok/NN/B-NP/O')]
--end of review.
start of review:
[Sentence('much/JJ/B-ADJP/O .../:/O/O')]
--end of review.
start of review:
[Sentence('high/NN/B-NP/O h

[Sentence("like/IN/B-PP/B-PNP Stallone/NNP/B-NP/I-PNP ,/,/O/O ,/,/O/O you\\/NN/B-NP/O 'll/MD/B-VP/O probably/RB/B-ADVP/O like/DT/B-NP/O movie/NN/I-NP/O ././O/O")]
[Sentence('Also/RB/B-ADVP/O ,/,/O/O per/IN/B-PP/O ending/VBG/B-VP/O ,/,/O/O looks/VBZ/B-VP/O like/DT/B-NP/O part/NN/I-NP/O 3/CD/B-NP/O point/NN/I-NP/O ././O/O')]
--end of review.
start of review:
[Sentence('thought/VBD/B-VP/O great/JJ/B-NP/O movie/NN/I-NP/O !/./O/O')]
--end of review.
start of review:
[Sentence('Terrible/NNP/B-NP/O ,/,/O/O awful/JJ/B-ADJP/O ,/,/O/O stupid/NNP/B-NP/O Hollywood/NNP/I-NP/O nonsense/NN/I-NP/O ././O/O')]
[Sentence("Always/RB/B-VP/O liked/VBD/I-VP/O Sly/JJ/B-ADJP/O ,/,/O/O sucked/VBD/B-VP/O right/NN/B-NP/O close/NN/I-NP/O ups/NNS/I-NP/O Sly/NNP/I-NP/O 's/POS/O/O lumpy/JJ/B-NP/O cheese/NN/I-NP/O curd/NN/I-NP/O face/NN/I-NP/O ././O/O")]
--end of review.
start of review:
[Sentence('thought/VBD/B-VP/O good/JJ/B-ADJP/O ,/,/O/O great/JJ/B-ADJP/O ,/,/O/O though/IN/B-PP/O good/JJ/B-ADJP/O')]
--end of revie

[Sentence('Can\\u2019t/NNP/B-NP/O recommend/VB/B-VP/O ,/,/O/O stick/VB/B-VP/O first/JJ/B-NP/O movie/NN/I-NP/O ././O/O')]
--end of review.
start of review:
[Sentence('Ok/NN/B-NP/O action/NN/I-NP/O ././O/O')]
[Sentence('Kind/NN/B-NP/O cheesy/JJ/I-NP/O story/NN/I-NP/O line/NN/I-NP/O though/RB/B-ADVP/O ././O/O')]
--end of review.
start of review:
[Sentence("story/NN/B-NP/O n't/RB/B-VP/O make/VB/I-VP/O sense/NN/B-NP/O ././O/O")]
--end of review.
start of review:
[Sentence('Nice/JJ/B-NP/O movie/NN/I-NP/O')]
--end of review.
start of review:
[Sentence('Awesome/JJ/B-NP/O movie/NN/I-NP/O')]
--end of review.
start of review:
[Sentence('first/JJ/B-ADJP/O one/CD/O/O much/RB/B-ADJP/O nicer/JJR/I-ADJP/O')]
--end of review.
start of review:
[Sentence('Pretty/RB/B-NP/O good/JJ/I-NP/O action/NN/I-NP/O movie/NN/I-NP/O ././O/O')]
[Sentence('Stallone/NNP/B-NP/O fine/JJ/B-ADJP/O ././O/O')]
--end of review.
start of review:
[Sentence("Trust/NNP/B-NP/O bad/JJ/I-NP/O reviews/NNS/I-NP/O ,/,/O/O n't/JJ/B-ADJP/O

...

[Sentence('reruns/NNS/B-NP/O years/NNS/I-NP/O ,/,/O/O conventions/NNS/B-NP/O ,/,/O/O made/VBN/B-VP/O screen/NN/B-NP/O come/NN/I-NP/O back/RB/B-ADVP/O ././O/O')]
[Sentence('looking/VBG/B-VP/O bumbling/JJ/B-ADJP/O comedy/VBG/B-VP/O reluctant/JJ/B-NP/O heroes/NNS/I-NP/O worth/JJ/B-NP/O watch/NN/I-NP/O ././O/O')]
--end of review.
start of review:
[Sentence("could/MD/B-VP/O n't/RB/I-VP/O stop/VB/I-VP/O watching/VBG/I-VP/O ,/,/O/O unlikely/JJ/B-NP/O plot/NN/I-NP/O ,/,/O/O corniest/JJS/B-NP/O class/NNP/I-NP/O B/NNP/I-NP/O movie/NN/I-NP/O graphics/NNS/I-NP/O ,/,/O/O crew/VBG/B-VP/O top/JJ/B-NP/O stars/NNS/I-NP/O working/VBG/B-VP/O well/RB/I-VP/O together/RB/I-VP/O make/VB/I-VP/O slapstick/NN/B-NP/O storyline/NN/I-NP/O come/NN/I-NP/O life/NN/I-NP/O ././O/O")]
[Sentence("Tim/NNP/B-NP/O Allen/NNP/I-NP/O 's/POS/O/O hoot/NN/B-NP/O !/./O/O")]
--end of review.
start of review:
[Sentence("honestly/JJ/B-ADJP/O don\\'t/VBG/B-VP/O think/VBP/I-VP/O spoof/VBG/I-VP/O could/MD/I-VP/O done/VB/I-VP/O better/JJ

start of review:
[Sentence('\\/NN/B-NP/O "/"/O/O Galaxy/NNP/B-NP/O Quest"ALMOST/NNP/I-NP/O makes/VBZ/B-VP/O ;/:/O/O idea/NN/B-NP/O bunch/VBG/B-VP/O has-been/JJ/B-NP/O actors/NNS/I-NP/O TV/VBP/B-VP/O Sci-Fi/JJ/B-NP/O series/NN/I-NP/O save/NN/I-NP/O universe/NN/I-NP/O \\\'for/NN/I-NP/O real\\/NN/I-NP/O \'/POS/O/O funny/JJ/B-ADJP/O ,/,/O/O Tim/NNP/B-NP/O Allen/NNP/I-NP/O ,/,/O/O Sigourney/NNP/B-NP/O Weaver/NNP/I-NP/O marvellous/NNP/I-NP/O Alan/NNP/I-NP/O Rickman/NNP/I-NP/O terrific/JJ/B-ADJP/O roles/VBZ/B-VP/O mis-matched/JJ/B-NP/O losers/NNS/I-NP/O forking/VBG/B-VP/O scant/JJ/B-NP/O living/NN/I-NP/O making/VBG/B-VP/O personal/JJ/B-ADJP/O appearances/VBZ/B-VP/O Sci-Fi/JJ/B-NP/O conventions/NNS/I-NP/O ././O/O')]
[Sentence("However/RB/B-ADVP/O ,/,/O/O subtext/NN/B-NP/O established/VBN/B-VP/O -/:/O/O forgotten/VBN/B-VP/O ,/,/O/O we\\/NN/B-NP/O 're/VBP/B-VP/O left/VBN/I-VP/O typical/JJ/B-NP/O \\'laser-gun&slash;scary/JJ/I-NP/O alien&slash;big/NN/I-NP/O explotion\\/NN/I-NP/O '/POS/O/O type/NN/

[Sentence('least/JJS/B-NP/O bit/NN/I-NP/O familiar/NNP/I-NP/O Star/NNP/I-NP/O Trek/NNP/I-NP/O TV/NN/I-NP/O shows/VBZ/B-VP/O and&slash;or/NN/B-NP/O films/NNS/I-NP/O ,/,/O/O Galaxy/NNP/B-NP/O Quest/NNP/I-NP/O busting/VBG/B-VP/O gut!,many/NN/B-NP/O highlights/VBZ/B-VP/O mention/VBN/I-VP/O individually/RB/B-ADVP/O ,/,/O/O simply/JJ/B-ADJP/O need/VBG/B-VP/O watch/NN/B-NP/O ././O/O')]
[Sentence('familiar/NNP/B-NP/O Star/NNP/I-NP/O Trek/NNP/I-NP/O franchise/NN/I-NP/O look/NN/I-NP/O oddly/RB/B-VP/O doubled/VBD/I-VP/O laughing/VBG/I-VP/O ././O/O')]
[Sentence('attempt/NN/B-NP/O watch/NN/I-NP/O people/NNS/I-NP/O ,/,/O/O ruin/NN/B-NP/O experience/NN/I-NP/O ././O/O')]
--end of review.
start of review:
[Sentence('movie/NN/B-NP/O funny/JJ/B-ADJP/O ,/,/O/O touching/VBG/B-VP/O ,/,/O/O little/JJ/B-NP/O way/NN/I-NP/O ,/,/O/O deep/JJ/B-ADJP/O ././O/O')]
[Sentence('idea/NN/B-NP/O has-been/JJ/B-ADJP/O ,/,/O/O sci-fi-TV-show/JJ/B-NP/O actors/NNS/I-NP/O idolized/JJ/B-NP/O race/NN/I-NP/O aliens/NNS/I-NP/O tech

start of review:
[Sentence('fun/NN/B-NP/O movie/NN/I-NP/O watch/NN/I-NP/O like/IN/B-PP/B-PNP Star/NNP/B-NP/I-PNP Trek/NNP/I-NP/I-PNP space/NN/I-NP/I-PNP movies/NNS/I-NP/I-PNP ././O/O')]
[Sentence('watch/VB/B-VP/O gets/VBZ/I-VP/O funnier/JJR/B-ADJP/O watch/VB/B-VP/O ././O/O')]
--end of review.
start of review:
[Sentence('Actors/NNS/B-NP/O believable/JJ/B-ADJP/O ,/,/O/O dialog/NN/B-NP/O well-written/JJ/B-ADJP/O ,/,/O/O movie/NN/B-NP/O moves/NNS/I-NP/O good/JJ/I-NP/O pace/NN/I-NP/O ././O/O')]
[Sentence('Good/JJ/B-NP/O combination/NN/I-NP/O science/NN/I-NP/O fiction/NN/I-NP/O comedy--well/JJ/B-NP/O worth/JJ/I-NP/O seeing/NN/I-NP/O ././O/O')]
--end of review.
start of review:
[Sentence('picky/JJ/B-NP/O movies/NNS/I-NP/O ././O/O')]
[Sentence("perfect/JJ/B-NP/O satire/NNP/I-NP/O Star/NNP/I-NP/O Trek/NNP/I-NP/O shows/VBZ/B-VP/O it\\/NN/B-NP/O 's/POS/O/O fans/NNS/B-NP/O ;/:/O/O flawless/JJ/B-ADJP/O ././O/O")]
[Sentence('Tim/NNP/B-NP/O Alan/NNP/I-NP/O perfect/NNP/I-NP/O Bill/NNP/I-NP/O Shatner/N

[Sentence('skeptical/JJ/B-ADJP/O ,/,/O/O worried/VBN/B-VP/O mistake/NN/B-NP/O rented/VBN/B-VP/O anyway/RB/B-ADVP/O ././O/O')]
[Sentence('Well/UH/O/O ,/,/O/O ././O/O')]
[Sentence('puns/NNS/B-NP/O sidejokes/NNS/I-NP/O running/VBG/B-VP/O throughout/DT/B-NP/O flick/NN/I-NP/O ././O/O')]
[Sentence('Whenever/WRB/B-ADVP/O need/NN/B-NP/O good/JJ/I-NP/O laugh/NN/I-NP/O pop/NN/I-NP/O ././O/O')]
[Sentence('Whether/IN/B-PP/B-PNP sci-fci/JJ/B-NP/I-PNP fan/NN/I-NP/I-PNP enjoy/NN/I-NP/I-PNP movie/NN/I-NP/I-PNP ././O/O')]
--end of review.
start of review:
[Sentence('Good/JJ/B-NP/O entertainment/NN/I-NP/O ,/,/O/O especially/RB/B-ADVP/O Star/NNP/B-NP/O Trek/NNP/I-NP/O fans/NNS/I-NP/O ././O/O')]
[Sentence("Many/JJ/B-NP/O funny/JJ/I-NP/O moments/NNS/I-NP/O fun/VBP/B-VP/O original/JJ/B-NP/O series/NN/I-NP/O expendable/JJ/B-NP/O crew/NN/I-NP/O member/NN/I-NP/O captain/NN/I-NP/O 's/POS/O/O shirt/NN/B-NP/O torn/VBN/B-VP/O ././O/O")]
--end of review.
start of review:
[Sentence('Love/NNP/B-NP/O send/VB/B-VP/O ge

**The preceding output is a somewhat raw shallow-parsed sentence tree for our sample sentence.**

In [27]:
# a more readable format -- depict each phrase and its internal constituents
for document in df_reviews_list[1:10]:
    tokens_list = tokenize_text(document)
#     print tokens
    filtered_list = [remove_stopwords(token) for token in tokens_list]
    filtered_document = detokenize (filtered_list) 
    # start np chunk with parsetree 
    sentences = nltk.sent_tokenize(filtered_document)
    
    print ("start of review:")
    for sentence in sentences:
        tree = parsetree(sentence)
#         print type(tree)
        # Get chunks in an easier-to-understand format:
        # print all chunks
        for sentence_tree in tree:
#             print (sentence_tree.chunks)
            for chunk in sentence_tree.chunks:
                print chunk.type, '->', [(word.string, word.type)
                                        for word in chunk.words]
                # get various constituents of the parse tree
#                 def get_sentence_tree_constituents(sentence_tree):
#                 print ("various constituents of the parse tree --", sentence_tree.constituents())
    print ("--end of review:")
           

start of review:
NP -> [(u'\\', u'NN')]
NP -> [(u'one', u'CD'), (u'star"reviews', u'NNS')]
VP -> [(u'lowered', u'VBD')]
NP -> [(u'expectations', u'NNS')]
NP -> [(u'first', u'JJ'), (u'second', u'JJ'), (u'series', u'NNP'), (u'Escape', u'NNP'), (u'Plan', u'NNP'), (u'franchise', u'NN')]
ADJP -> [(u'really', u'RB'), (u'good', u'JJ')]
VP -> [(u'definitely', u'RB'), (u'missed', u'VBD')]
NP -> [(u'high', u'JJ'), (u'mark', u'NN')]
ADVP -> [(u'However', u'RB')]
NP -> [(u'everyone', u'NN')]
VP -> [(u'dogged', u'VBD')]
NP -> [(u'movie', u'NN')]
VP -> [(u'watched', u'VBD')]
NP -> [(u'simplified', u'JJ'), (u'mind', u'NN')]
NP -> [(u'great', u'JJ'), (u'movie', u'NN')]
--end of review:
start of review:
NP -> [(u'first', u'JJ'), (u'good', u'JJ'), (u'opinion', u'NN')]
NP -> [(u'record', u'NNP'), (u'Stallone', u'NNP'), (u'Bautista', u'NNP')]
VP -> [(u'appear', u'VB')]
PP -> [(u'throughout', u'IN')]
NP -> [(u'whole', u'JJ'), (u'movie', u'NN')]
--end of review:
start of review:
VP -> [(u'watching', u'VBG')

In [28]:
# process the shallow parsed tree into an easy to understand format
from pattern.en import parsetree, Chunk
from nltk.tree import Tree

def process_sentence_tree(sentence_tree):
    tree_constituents = sentence_tree.constituents()
    
    processed_tree = [(item.type,[(w.string, w.type) for w in item.words])
                       
                        if type(item) == Chunk # from pattern.en import parsetree, Chunk
                        else ('-',[(item.string, item.type)] )
                             for item in tree_constituents 
                        ] 
    return processed_tree 


In [29]:
# print the sentence tree using nltk's Tree syntax
def print_sentence_tree(sentence_tree):
    processed_tree = process_sentence_tree(sentence_tree)
    processed_tree = [
                        Tree( item[0],
                             [
                                 Tree(x[1], [x[0]])
                                 for x in item[1]
                             ]
)
                            for item in processed_tree
                     ]
    tree = Tree('S', processed_tree )
    print tree

In [30]:
# visualize the sentence tree using nltk's Tree syntax
def visualize_sentence_tree(sentence_tree):
    processed_tree = process_sentence_tree(sentence_tree)
    processed_tree = [
                        Tree( item[0],
                             [
                                 Tree(x[1], [x[0]])
                                 for x in item[1]
                             ]
)
                            for item in processed_tree
                     ]
    tree = Tree('S', processed_tree )
    tree.draw()

In [31]:
# Visualize a couples of np-chunked sentences
for document in df_reviews_list[1:2]:
    tokens_list = tokenize_text(document)
#     print tokens
    filtered_list = [remove_stopwords(token) for token in tokens_list]
    filtered_document = detokenize (filtered_list) 
    # start np chunk with parsetree 
    sentences = nltk.sent_tokenize(filtered_document)

    for sentence in sentences:
        tree = parsetree(sentence)
#         print type(tree)
        # Get chunks in an easier-to-understand format:
        # print all chunks
        for sentence_tree in tree:
#             print (sentence_tree.chunks)
#             for chunk in sentence_tree.chunks:
#                 print chunk.type, '->', [(word.string, word.type)
#                                         for word in chunk.words]
                # get various constituents of the parse tree
#                 def get_sentence_tree_constituents(sentence_tree):
#                 print ("various constituents of the parse tree --", sentence_tree.constituents())
           
            visualize_sentence_tree(sentence_tree)

<a id="result"></a>

# Question 3: 

### Web Scraping Method Summary: 

I go to Amazon website @https://www.amazon.com/, then choose "Movies & TV" from the Department Drop Down menu to get to @https://www.amazon.com/gp/browse.html?node=2625373011&ref_=nav_em_T1_0_4_14_1__mov. From this page, I chose Action Movie genre and this brings me to @https://www.amazon.com/action-adventure-dvd-bluray/b/ref=MoviesHPBB_Genres_Action?ie=UTF8&node=2650363011&pf_rd_m=ATVPDKIKX0DER&pf_rd_s=merchandised-search-left-3&pf_rd_r=PKNMMEERDZVDM36D5QSC&pf_rd_r=PKNMMEERDZVDM36D5QSC&pf_rd_t=101&pf_rd_p=f1849530-129c-4959-9d34-94ca73a3e67e&pf_rd_p=f1849530-129c-4959-9d34-94ca73a3e67e&pf_rd_i=2625373011. 

In this link, there is node number (specific for each category in Amazon). I use this number and the pf_rd_i number to cycle through the pages that list all the movies and its unique ASIN, an Amazon product identification. Amazon has all their product reviews under page @"https://www.amazon.com/product-reviews/" with the format of "https://www.amazon.com/product-reviews/" + ASIN. 

I save all my ASIN for all the action movies available to watch on Amazon in file "AcMovie_asin_clean.cvs". There are 
144 movies with a total of 146072 reviews. Each movie has its own page @https://www.amazon.com/product-reviews/, e.g: Transformers: The Last Knight by Mark Wahlberg is at: https://www.amazon.com/product-reviews/B07215NWRL. This movie has 1,512 reviews (in 152 pages). 

For the purchase of this exercise, I only scrap 1000 urls of 8 movies, total of 9923 individual reviews. 
The complete copy of all the urls for all reviews of all 144 action movies on Amazon is in the file "Movies_urls_all.cvs"

Below are some statistics about the Action and advanture genre, its urls, its customer reviews. 

## Output of the NP-chunk:

NP is the majority sense in my downloaded action movie reviews. However, there are not alot of proper names in the reviews. Majority of reviews are short, 2-3 sentences each. 

The NP chunk was not as nice and difficutle to read before normalizing and removing stopwords. So the pre-processing is necessary. For the next project, POS tagging may be considered in the pre-preprocessing step. 
      
 <a href="#top">Back to top</a>

**Some statistics on the Action and Advanture genre**

In [18]:
# some statistics on the genre
df_asin_ACmovie.info()
df_asin_ACmovie.describe()
df_asin_ACmovie.head()
df_asin_ACmovie.num_review.sum(), 
df_asin_ACmovie.rating.mean(), 
df_asin_ACmovie.rating.median(),

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 144 entries, 0 to 143
Data columns (total 6 columns):
ASIN            144 non-null object
category        144 non-null object
company         144 non-null object
num_review      144 non-null int64
product_desc    144 non-null object
rating          144 non-null float64
dtypes: float64(1), int64(1), object(4)
memory usage: 6.8+ KB


num_review      rating
count   144.000000  144.000000
mean   1014.388889    4.031250
std     951.537072    0.521089
min     138.000000    2.600000
25%     356.500000    3.875000
50%     608.500000    4.100000
75%    1416.250000    4.400000
max    3550.000000    4.800000

ASIN     category company  num_review                   product_desc  \
0  B07D2KJGB9  Movies & TV       R         407           Escape Plan 2: Hades   
1  B07F19R3D9  Movies & TV   PG-13         138           Ant-Man and the Wasp   
2  B07215NWRL  Movies & TV   PG-13        1510  Transformers: The Last Knight   
3  B003WJ6AD2  Movies & TV      PG        1576                         Legend   
4  B001I8458G  Movies & TV   PG-13         650                      Get Smart   

   rating  
0     2.6  
1     3.9  
2     3.4  
3     4.3  
4     4.4

(146072,)

(4.0312499999999964,)

(4.1,)

**There are 144 Action movies available for watching on Amazon. Total number of reviews is 146,072. The mean rating score is 4.03 out of 5, the median rating score is 4.1**

In [19]:
df_urls_movie.info()
df_urls_movie.describe()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14544 entries, 0 to 14543
Data columns (total 2 columns):
page_urls    14544 non-null object
ASIN         14544 non-null object
dtypes: object(2)
memory usage: 227.3+ KB


page_urls        ASIN
count                                               14544       14544
unique                                               1616          16
top     https://www.amazon.com/product-reviews/B07H8XM...  B07816TG17
freq                                                    9        3195

**There are 14544 pages (or urls) of customer reviews for all these 144 movies** 